## What are We Building? A Dataloader 

We need to create an efficient data loading method to train the image classification algorithm that automates preprocessing the images and assigning labels to the training samples. In this article, we perform image classification on the CIFAR-10 dataset.

A typical split for the CIFAR-10 dataset uses 50,000 images for training and 10,000 for testing.

We are using the CIFAR-10 dataset, which contains a total of 60000 32x32 RGB images with 10 classes.

In [7]:
import pickle
import numpy as np
from PIL import Image
import torch
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from torchvision import transforms
import os

In [ ]:
transform = transforms.Compose([
    transforms.Resize(200),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.4914, 0.4822, 0.4465],
                         std=[0.2023, 0.1994, 0.2010]),
    transforms.RandomErasing(),
    transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2, hue=0.2),
    transforms.RandomAffine(degrees=45, translate=(0.2, 0.2), scale=(0.8, 1.2), shear=45),
    transforms.RandomPerspective(),
])


The main Dataloader have the following structure: They are composed of a
* `__len__` for the length of the class
* `__getitem__` to retrive the items in the class

In [56]:
class cifar10(Dataset):
    def  __init__(self, *args):
        # initialize dataset variables here
        self.root = root
        
    def  __len__(self):
        # returns the length of the dataset 
        return None    
        
    def __getitem__(self, index):
        
        # preprocess and transformations
        # indexes the dataset such that dataset[i] can retrieve the ith sample.
        return image, label

from torchvision.datasets import CIFAR10

# The CIFAR10 in itself is already a Dataset class, so you need to apply the transform here

cifar = CIFAR10(root='data', download=True, transform=transform)
print(type(cifar))

Files already downloaded and verified
<class 'torchvision.datasets.cifar.CIFAR10'>


In [ ]:
# apply the transforms to an image
print(cifar[1][0])
image = cifar[1][0]
transformed_image = transform(image)
transformed_image

For every **New Dataset** has their own unique way of displaying the data and so you need to see the Dataloader for each specific dataset you have. Let's discover how the CIFAR dataset is displayed. In this case is important also to understand what kind of **Data Type** you have in front in you, to know how better to implement what you need to do, in out case the CIFAR or in better `torch.utils.data.Dataset` is a Class, so easily we can know the shape of the data via: 

When in doubt of what kind of datatype you have in front of view you can use: `type(object)` or `vars(object)` to understanf the insides of class

In [47]:
print("Format of the data: {}".format(cifar.data.shape))
print("Data Type of the Inputs data: {}".format(type(cifar.data)))
print("Format of the labels: {}".format(len(cifar.targets)))
print("Data Type of the Output data: {}".format(type(cifar.targets)))

Format of the data: (50000, 32, 32, 3)
Data Type of the Inputs data: <class 'numpy.ndarray'>
Format of the labels: 50000
Data Type of the Output data: <class 'list'>


In [3]:
class cifar10(Dataset):
	def __init__(self, root, train = False, transforms = None):
        # Variables for the dataset
		self.root = root
		self.transforms = transforms
		self.train = train

        # Splitting the dataset into training and test data 
		self.train_data = [file for file in os.listdir(root) if "data_batch" in file]
		self.test_data = [file for file in os.listdir(root) if "test_batch" in file]

		self.data_files = self.train_data if self.train else self.test_data
		# we will read the images and labels and store them in these lists.
		self.images = [] # -> list
		self.labels = [] # -> list
		
		self.load_data()


	def __len__(self):
		# this returns and only returns the length of the dataset
		return len(self.images)

	def __getitem__(self, idx):

		if torch.is_tensor(idx):
			idx = idx.tolist()

        # retrieve the image from the list created of the dataset
		image = self.images[idx]
		image = Image.fromarray(image) # -> return it as an image

		label = self.labels[idx]  # -> get the labels of the image

		if self.transforms:
			image = self.transforms(image)   # apply any transformation

		return image, label  # -> return the image and the labels as a tuple


	def load_data(self):

		for file in self.data_files:
			file_path = os.path.join(self.root, file)
			sample = self.read_file(file_path)
			self.images.append(sample["data"])
			self.labels.extend(sample["labels"])


		self.images = np.vstack(self.images).reshape(-1, 3, 32, 32)
		self.images = self.images.transpose((0, 2, 3, 1))

	def read_file(self, filename):
		with open(filename, "rb") as f:
			f = pickle.load(f, encoding = "latin1")
		return f


In [57]:
data_loader = torch.utils.data.DataLoader(cifar,batch_size=4,shuffle=False)
data_loader

for batch_idx, samples in enumerate(data_loader):
      print(batch_idx, samples)

0 [tensor([[[[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.9717, 0.5247, 0.0861],
          [0.0000, 0.0000, 0.0000,  ..., 0.4759, 0.0618, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.4272, 0.0131, 0.0000]],

         [[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.8761, 0.2791, 0.0458],
          [0.0000, 0.0000, 0.0000,  ..., 0.2531, 0.0329, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.2272, 0.0069, 0.0000]],

         [[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ...

In [7]:
print(torch.hub.help('pytorch/vision', 'resnet18', force_reload=True))

Downloading: "https://github.com/pytorch/vision/zipball/main" to /home/helldiver/.cache/torch/hub/main.zip


ResNet-18 from `Deep Residual Learning for Image Recognition <https://arxiv.org/abs/1512.03385>`__.

    Args:
        weights (:class:`~torchvision.models.ResNet18_Weights`, optional): The
            pretrained weights to use. See
            :class:`~torchvision.models.ResNet18_Weights` below for
            more details, and possible values. By default, no pre-trained
            weights are used.
        progress (bool, optional): If True, displays a progress bar of the
            download to stderr. Default is True.
        **kwargs: parameters passed to the ``torchvision.models.resnet.ResNet``
            base class. Please refer to the `source code
            <https://github.com/pytorch/vision/blob/main/torchvision/models/resnet.py>`_
            for more details about this class.

    .. autoclass:: torchvision.models.ResNet18_Weights
        :members:
    
